# Main Notebook

In [7]:
import os
import gc
import pytz
import operator
import numpy as np
import pickle as pkl
from time import sleep
from datetime import datetime
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn import preprocessing
import tensorflow as tf
from tensorflow import math
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.models import Sequential
from tensorflow.keras.activations import relu, elu
from tensorflow.keras.layers import Dense, Dropout
from talos.model import early_stopper
import talos
import warnings
warnings.filterwarnings('ignore')
warnings.filterwarnings(action = 'ignore', category = FutureWarning)
warnings.filterwarnings(action = 'ignore', category = DeprecationWarning)

import pandas as pd
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)

import sys
sys.path.append('..')

time = datetime.now(pytz.timezone('Europe/Oslo')).strftime('%m.%d.%Y_%H.%M.%S')
print(f'Notebook initialized execution at {time}.')
#import xgboost as xgb

Notebook initialized execution at 03.04.2020_15.19.57.


## General Methods

In [8]:
def memory_optimization(dfs):
    for df in dfs:
        del df
    gc.collect()

## Prepare Data

In [9]:
import datasets

start_time = datetime.now()

scaler = MinMaxScaler()

train_x, train_y, validation_x, validation_y, test_x, test_y, scaler = datasets.load(f'../input/finn.csv', scaler)

print(train_x)

       Soverom  Primærrom  Bruksareal   Byggeår       Rom  parkering  fiber  \
825   0.068182   0.122353    0.138289  0.994203  0.242424        1.0    0.0   
618   0.045455   0.078824    0.061366  0.907246  0.060606        1.0    0.0   
1388  0.136364   0.224706    0.206569  0.727536  0.181818        1.0    0.0   
69    0.090909   0.163529    0.154710  0.971014  0.151515        1.0    0.0   
1410  0.068182   0.103529    0.078652  0.991304  0.090909        1.0    0.0   
29    0.045455   0.098824    0.076059  0.202899  0.060606        0.0    0.0   
2918  0.113636   0.122353    0.096802  0.973913  0.121212        1.0    0.0   
2390  0.068182   0.176471    0.170268  0.800000  0.090909        1.0    0.0   
3020  0.068182   0.137647    0.102852  0.756522  0.212121        1.0    0.0   
1691  0.090909   0.148235    0.108902  0.979710  0.121212        1.0    1.0   
991   0.068182   0.109412    0.092481  0.855072  0.090909        1.0    0.0   
1487  0.068182   0.117647    0.127917  0.721739  0.0

# Optimization Parameters

In [10]:
parameters = {'activation_1':['relu', 'elu'],
     'activation_2':['relu', 'elu'],
     'optimizer': ['Adam', "RMSprop"],
     'loss-functions': ['mse'],
     'neurons_HL1': [50, 100, 200],
     'neurons_HL2': [40, 80, 160],
     'dropout1': [0.1, 0.2, 0.3],
     'dropout2': [0.1, 0.2, 0.3],
     'batch_size': [100, 500, 1000],
     'epochs': [10, 15, 900],
     'losses': ['mse']
}

In [11]:
def talolos(x_train, y_train, x_val, y_val, parameters):
    model = Sequential()

    model.add(Dense(parameters['neurons_HL1'], 
    input_shape=(train_x.shape[1],), 
    activation=parameters['activation_1'],use_bias=True))

    model.add(Dropout(0.2))

    model.add(Dense(parameters['neurons_HL2'], 
    activation=parameters['activation_2'], use_bias=True))

    model.add(Dropout(0.1))

    model.add(Dense(1, activation='relu'))

    model.compile(optimizer=parameters['optimizer'], loss=parameters['losses'], 
    metrics=['mse'])

    history = model.fit(x_train, y_train,
            batch_size=parameters['batch_size'],epochs=parameters['epochs'],
            verbose=1,validation_data=[x_val, y_val],
            callbacks=[early_stopper(epochs=parameters['epochs'], 
            mode='moderate',monitor='val_loss')])
    
    return history, model

## Specify model

In [14]:
t = talos.Scan(x=np.array(train_x),
               y=np.array(train_y),
               x_val=np.array(validation_x),
               y_val=np.array(validation_y),
               model=talolos,
               params=parameters,
               experiment_name='oloo',
               round_limit=100)


  0%|          | 0/100 [00:00<?, ?it/s]

Train on 2770 samples, validate on 347 samples
Epoch 1/10
2770/2770 [==============================] - 0s 60us/sample - loss: 0.0307 - mean_squared_error: 0.0307 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 2/10
2770/2770 [==============================] - 0s 19us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 3/10
2770/2770 [==============================] - 0s 18us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276



  1%|          | 1/100 [00:00<01:18,  1.26it/s]

Train on 2770 samples, validate on 347 samples
Epoch 1/10
2770/2770 [==============================] - 0s 64us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 2/10
2770/2770 [==============================] - 0s 23us/sample - loss: 0.0304 - mean_squared_error: 0.0304 - val_loss: 0.0276 - val_mean_squared_error: 0.0276



  2%|▏         | 2/100 [00:01<01:16,  1.28it/s]

...


 99%|█████████▉| 99/100 [06:36<00:06,  6.12s/it]

Train on 2770 samples, validate on 347 samples
Epoch 1/900
2770/2770 [==============================] - 0s 46us/sample - loss: 0.0363 - mean_squared_error: 0.0363 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 2/900
2770/2770 [==============================] - 0s 8us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 3/900
2770/2770 [==============================] - 0s 10us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 4/900
2770/2770 [==============================] - 0s 8us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 5/900
2770/2770 [==============================] - 0s 9us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 6/900
2770/2770 [==============================] - 0s 8us/sample - loss: 0.0303 - mean_squared_error: 0.0303 -

Epoch 50/900
2770/2770 [==============================] - 0s 8us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 51/900
2770/2770 [==============================] - 0s 9us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 52/900
2770/2770 [==============================] - 0s 9us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 53/900
2770/2770 [==============================] - 0s 8us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 54/900
2770/2770 [==============================] - 0s 10us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 55/900
2770/2770 [==============================] - 0s 9us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error

Epoch 99/900
2770/2770 [==============================] - 0s 9us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 100/900
2770/2770 [==============================] - 0s 9us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 101/900
2770/2770 [==============================] - 0s 9us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 102/900
2770/2770 [==============================] - 0s 9us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 103/900
2770/2770 [==============================] - 0s 10us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_error: 0.0276
Epoch 104/900
2770/2770 [==============================] - 0s 8us/sample - loss: 0.0303 - mean_squared_error: 0.0303 - val_loss: 0.0276 - val_mean_squared_


100%|██████████| 100/100 [06:39<00:00,  3.99s/it]


In [15]:
print(t.data)

    round_epochs      loss  mean_squared_error  val_loss  \
0              3  0.030345            0.030345  0.027553   
1              2  0.030367            0.030367  0.027553   
2            323  0.002603            0.002603  0.002676   
3            528  0.001858            0.001858  0.003310   
4              2  0.030345            0.030345  0.027553   
5              4  0.008649            0.008649  0.005455   
6            139  0.030345            0.030345  0.027553   
7            379  0.000520            0.000520  0.002752   
8              2  0.030256            0.030256  0.027553   
9              6  0.009671            0.009671  0.005289   
10             2  0.030345            0.030345  0.027553   
11             2  0.030345            0.030345  0.027553   
12             4  0.034906            0.034906  0.027547   
13             3  0.030313            0.030313  0.027553   
14             3  0.030345            0.030345  0.027553   
15             4  0.030270            0.

In [32]:
t.plot_hist()

AttributeError: 'Scan' object has no attribute 'plot_hist'

In [31]:
t.best_model(metric='loss').predict(test_x)

ValueError: Unknown initializer: GlorotUniform

In [25]:
print(train_y.iloc[1])
for index in range(117):
    mat = np.zeros((1, 117))
    mat[0, index] = 0.0026
    print(scaler.inverse_transform(mat)[:,index])

0.14518351753026293
[205246.5688]
[0.1144]
[2.21]
[3.0082]
[1675.897]
[1.0858]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[0.0026]
[58.5312]
[-0.9636]
[10581.48]
[9109.9606]
[0.0156]
[0.0104]
[58.05869097]
[5.20883073]
[0.19033962]
[0.26]
[0.26]
[0.13]
[0.26]
[0.15935484]
[0.1637037]
[0.04911111]
[0.26]
[0.05515152]
[0.22608696]
[0.26]
[0.23762611]
[0.15935484]
[0.26]
[0.26]
[0.26]
[0.26]
[0.26]
[0.26]
[0.26]
[0.26]
[0.11283019]
[0.25539823]
[0.072]
[0.07428571]
[0.04333333]
[0.02910448]
[0.06990566]
[0.16095238]
[0.0626506]
[0.13]
[0.21272727]
[0.16095238]
[0.05542636]
[0.05811765]
[0.22148148]
[0.14828125]
[0.07428571]
[0.06066667]
[0.19132075]
[0.08]
[0.06664839]
[0.11818182]
[0.03436306]
[0.03584642]
[0.04814815]
[0.05426087]
[0.08666667]
[0.10214286]
[0.26]
[0.26]
[0.15166667]
[0.08666667]
[0.08489796]
[0.07694915]
[0.00236204]
[0.00246422]
[0.00244643]
[0.00233921]
[0.00238357]
[0

## Train model

In [ ]:
print('# Fit model on training data')
history = model.fit(train_x, train_y,
                    batch_size=64,
                    epochs=3,
                    validation_data=(validation_x, validation_y))

print('\nhistory dict:', history.history)

## Results

In [ ]:
results = model.evaluate(validation_x, validation_y, batch_size=64)
print(results.shape)

In [ ]:
print(results*train_y_scale)